<a href="https://colab.research.google.com/github/liz-lewis-manchester/CNM_2025_group_01/blob/main/tests/Test_case_3.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation
from IPython.display import HTML, display #for plotting multiple graphs in google colab

#Solver class
class AdvectionSolver:
  #Finite difference solver for the 1D advection equation: d(theta)/dt + U*d(theta)/dx = 0


    def __init__(self, L, dx, dt, T, U):
        self.L = L
        self.dx = dx
        self.dt = dt
        self.T = T
        self.U = U

        # Spatial grid
        self.x_new = np.arange(0, L+dx, dx)
        self.num_points = len(self.x_new)
        self.num_time_steps = int(self.T / self.dt)

        if self.U <= 0:
            raise ValueError("This solver assumes flow velocity U > 0.")

    def _solve_implicit(self, theta_initial, boundary_theta):
        """
        Implicit Upwind Scheme (Standard BTBS).
        Unconditionally stable.
        Equation: theta_i^{n+1} = (theta_i^n + C * theta_{i-1}^{n+1}) / (1 + C)
        """
        print(f"Using **Implicit Scheme (Standard BTBS)**.")

        theta = np.copy(theta_initial)
        N = self.num_points

        theta_history = np.zeros((self.num_time_steps + 1, N))
        theta_history[0, :] = theta

        C = abs(self.U) * self.dt / self.dx # Parameter C for the implicit formula
        divisor = 1.0 + C

        for n in range(self.num_time_steps):
            theta_next = np.zeros_like(theta)

            # Boundary Condition
            theta_next[0] = boundary_theta

            # Forward Substitution
            for i in range(1, N):
                numerator = theta[i] + C * theta_next[i-1]
                theta_next[i] = numerator / divisor

            theta = theta_next
            theta_history[n+1, :] = theta

        return theta_history

    def compute_solution(self, theta_initial, boundary_theta):

        return self._solve_implicit(theta_initial, boundary_theta)

#Test 3 set up and configuration
L = 20
T = 300
configs = [
{"U": 0.05, "dx": 0.2, "dt": 10.0, "label": "U=0.05, dx=0.2, dt=10"},
{"U": 0.10, "dx": 0.2, "dt": 10.0, "label": "U=0.10, dx=0.2, dt=10"},
{"U": 0.10, "dx": 0.1, "dt": 10.0, "label": "U=0.10, dx=0.1, dt=10"},
{"U": 0.10, "dx": 0.2, "dt": 5.0, "label": "U=0.10, dx=0.2, dt=5"}
]
theta = 250.0

#Loop through configs, extract data and display animcation separately
for cfg in configs:
  U, dx, dt, label = cfg["U"], cfg["dx"], cfg["dt"], cfg["label"]

  solver_A = AdvectionSolver(L, dx, dt, T, U)
  theta_initial = np.zeros_like(solver_A.x_new)
  theta_initial[0] = theta
  res_A = solver_A.compute_solution(theta_initial, boundary_theta=250.0)

  fig, ax = plt.subplots(figsize=(4,3))

  plt.rcParams["animation.html"] = "jshtml"
  plt.rcParams['figure.dpi'] = 150
  plt.ioff() # interactive off

  def animate(t):
    ax.clear()
    y = res_A[t]
    ax.plot(solver_A.x_new, y)
    ax.set_xlim(0,L)
    ax.set_ylim(0, 300)
    ax.set_title(f"{label}\nConcentration of pollutant at t = {dt*t} s", fontsize=10, verticalalignment='top')
    ax.set_xlabel("x (m)", fontsize=8)
    ax.set_ylabel("Concentration (µg/m³)", fontsize=8)

  anim=matplotlib.animation.FuncAnimation(fig, animate, frames=len(res_A))

  display(HTML(anim.to_jshtml())) #display each graph immidiately after generated

Using **Implicit Scheme (Standard BTBS)**.


Using **Implicit Scheme (Standard BTBS)**.


Using **Implicit Scheme (Standard BTBS)**.


Using **Implicit Scheme (Standard BTBS)**.
